In [5]:

# We can easily calculate distances between Org_airport_lat + Org_airport_long and Dest_airport_lat + Dest_airport_long
# Basedon this information, we can plot the routes of all flichts and then we can calcualte the most fly-over places (countries, states, etc.)


In [5]:

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
from haversine import haversine, Unit

df = pd.read_csv ('C:\\Users\\ryan_\\Desktop\\Briefcase\\PDFs\\1-ALL PYTHON & R CODE SAMPLES\\A - GITHUB\\Airports\\Airports.csv')

# Calculate the distance using the haversine formula
def calculate_distance(row):
    origin = (row['Org_airport_lat'], row['Org_airport_long'])
    destination = (row['Dest_airport_lat'], row['Dest_airport_long'])
    distance = haversine(origin, destination, unit=Unit.KILOMETERS)
    return distance

df['Distance_km'] = df.apply(calculate_distance, axis=1)

df = df.fillna(0)

# let's look at a random sample because processing all would take a very, very, very long time
sample = df.sample(n=2000)
print(sample.shape)
print(sample.head())


(2000, 16)
        Origin_airport Destination_airport     Origin_city Destination_city  \
336635             ATL                 DAL     Atlanta, GA       Dallas, TX   
219893             IAD                 BOS  Washington, DC       Boston, MA   
1036661            AUS                 ELP      Austin, TX      El Paso, TX   
372375             DTW                 DFW     Detroit, MI       Dallas, TX   
276165             HOU                 DAL     Houston, TX       Dallas, TX   

         Passengers  Seats  Flights  Distance   Fly_date  Origin_population  \
336635         3229   5550      111       721   7/1/2001            4432950   
219893         2656   8610       30       413   4/1/1992            8474182   
1036661        3089   6439       47       528   1/1/2008            1654100   
372375        12631  19312      142       987   9/1/2006            8969084   
276165        39459  58006      475       239  10/1/1991            3888584   

         Destination_population  Org_ai

In [6]:

import pandas as pd
import folium
from folium.plugins import AntPath


# Create a base map centered around the United States
m = folium.Map(location=[37.0902, -95.7129], zoom_start=4)

# Add routes to the map
for idx, row in sample.iterrows():
    origin = (row['Org_airport_lat'], row['Org_airport_long'])
    destination = (row['Dest_airport_lat'], row['Dest_airport_long'])
    folium.Marker(origin, tooltip="Origin").add_to(m)
    folium.Marker(destination, tooltip="Destination").add_to(m)
    # Add AntPath for better visualization of the route
    AntPath(
        locations=[origin, destination],
        color='blue',
        weight=2,
        opacity=0.8
    ).add_to(m)

# Save map to an HTML file
# m.save('routes_map.html')

# To display the map inline in a Jupyter notebook, use:
m


In [7]:

import geopandas as gpd

# Correct path to your shapefile
states_shapefile_path = r'C:\\Users\\ryan_\\Desktop\\Briefcase\\PDFs\\1-ALL PYTHON & R CODE SAMPLES\\A - GITHUB\\Airports\\ne_10m_admin_0_countries.shp'

# Load the shapefile
states = gpd.read_file(states_shapefile_path)

# Inspect the columns
print(states.columns)

# Display the first few rows to understand the structure of the data
print(states.head())

# Display more detailed information about the GeoDataFrame
print(states.info())

# If columns are missing, check the presence of the .dbf file
import os

# Path to the directory containing the shapefile
directory = r'C:\\Users\\ryan_\\Desktop\\Briefcase\\PDFs\\1-ALL PYTHON & R CODE SAMPLES\\A - GITHUB\\Airports\\'

# List all files in the directory
files = os.listdir(directory)
print(files)


Index(['ADM0_A3_DE', 'featurecla', 'scalerank', 'LABELRANK', 'SOVEREIGNT',
       'SOV_A3', 'ADM0_DIF', 'LEVEL', 'TYPE', 'TLC',
       ...
       'FCLASS_TR', 'FCLASS_ID', 'FCLASS_PL', 'FCLASS_GR', 'FCLASS_IT',
       'FCLASS_NL', 'FCLASS_SE', 'FCLASS_BD', 'FCLASS_UA', 'geometry'],
      dtype='object', length=169)
  ADM0_A3_DE       featurecla  scalerank  LABELRANK SOVEREIGNT SOV_A3  \
0        IDN  Admin-0 country          0          2  Indonesia    IDN   
1        MYS  Admin-0 country          0          3   Malaysia    MYS   
2        CHL  Admin-0 country          0          2      Chile    CHL   
3        BOL  Admin-0 country          0          3    Bolivia    BOL   
4        PER  Admin-0 country          0          2       Peru    PER   

   ADM0_DIF  LEVEL               TYPE TLC      ADMIN ADM0_A3  GEOU_DIF  \
0         0      2  Sovereign country   1  Indonesia     IDN         0   
1         0      2  Sovereign country   1   Malaysia     MYS         0   
2         0      2  So

In [8]:

import pandas as pd
import geopandas as gpd
from shapely.geometry import LineString
from haversine import haversine, Unit
from rtree import index

# Load the airport data
df = pd.read_csv('C:\\Users\\ryan_\\Desktop\\Briefcase\\PDFs\\1-ALL PYTHON & R CODE SAMPLES\\A - GITHUB\\Airports\\Airports.csv')


# Sample the data
sample_size = 1000  # Adjust this number as needed
df_sampled = df.sample(n=sample_size, random_state=1)

# Load US state boundaries shapefile
states_shapefile_path = 'C:\\Users\\ryan_\\Desktop\\Briefcase\\PDFs\\1-ALL PYTHON & R CODE SAMPLES\\A - GITHUB\\Airports\\ne_10m_admin_0_countries.shp'
states = gpd.read_file(states_shapefile_path)

# Calculate the distance using the haversine formula
def calculate_distance(row):
    origin = (row['Org_airport_lat'], row['Org_airport_long'])
    destination = (row['Dest_airport_lat'], row['Dest_airport_long'])
    distance = haversine(origin, destination, unit=Unit.KILOMETERS)
    return distance

df_sampled['Distance_km'] = df_sampled.apply(calculate_distance, axis=1)

# Filter out rows with NaN coordinates
df_sampled = df_sampled.dropna(subset=['Org_airport_lat', 'Org_airport_long', 'Dest_airport_lat', 'Dest_airport_long'])

# Create a GeoDataFrame for flight paths
def create_flight_path(row):
    try:
        return LineString([(row['Org_airport_long'], row['Org_airport_lat']), (row['Dest_airport_long'], row['Dest_airport_lat'])])
    except Exception as e:
        print(f"Error creating LineString for row {row.name}: {e}")
        return None

flight_paths = df_sampled.apply(create_flight_path, axis=1)
flight_paths_gdf = gpd.GeoDataFrame(df_sampled, geometry=flight_paths)

# Drop rows where geometry creation failed
flight_paths_gdf = flight_paths_gdf.dropna(subset=['geometry'])

# Ensure the same CRS (Coordinate Reference System)
flight_paths_gdf.crs = states.crs

# Build the spatial index for states
state_idx = index.Index()
for pos, state in states.iterrows():
    state_idx.insert(pos, state['geometry'].bounds)

# Check for intersections and count the number of flights per state
state_flight_counts = {state: 0 for state in states['NAME']}
for _, flight in flight_paths_gdf.iterrows():
    flight_bounds = flight['geometry'].bounds
    possible_matches_index = list(state_idx.intersection(flight_bounds))
    possible_matches = states.iloc[possible_matches_index]
    for _, state in possible_matches.iterrows():
        try:
            if flight['geometry'].intersects(state['geometry']):
                state_flight_counts[state['NAME']] += 1
        except Exception as e:
            print(f"Error checking intersection for flight {flight.name} and state {state['NAME']}: {e}")

# Convert the results to a DataFrame for easier analysis
flight_counts_df = pd.DataFrame(list(state_flight_counts.items()), columns=['State', 'Flight_Count'])
flight_counts_df = flight_counts_df.sort_values(by='Flight_Count', ascending=False)

print(flight_counts_df)

# Save the results to a CSV file if needed
flight_counts_df.to_csv('C:\\Users\\ryan_\\Desktop\\state_flight_counts.csv', index=False)
print(flight_counts_df.head())


                                State  Flight_Count
154                            Canada           995
155                            Mexico            81
156                            Belize             3
157                            Panama             0
159                  Papua New Guinea             0
160                             Egypt             0
161                             Yemen             0
162                        Mauritania             0
163                        Eq. Guinea             0
164                            Gambia             0
165                         Hong Kong             0
166                           Vatican             0
167                          Akrotiri             0
168                         Bir Tawil             0
169                        Antarctica             0
170                         Australia             0
171                         Greenland             0
172                              Fiji             0
173         

In [ ]:

# Data sources:

# https://www.kaggle.com/datasets/flashgordon/usa-airport-dataset?resource=download

# The .shx file associated with the ne_10m_admin_0_countries.shp and the .shx file are both essential for reading the shapefile because the .shx 
# contains the index data for the geometry.

# https://github.com/nvkelso/natural-earth-vector/blob/master/10m_cultural/ne_10m_admin_0_countries.shx
# https://github.com/nvkelso/natural-earth-vector/blob/master/10m_cultural/ne_10m_admin_0_countries.shp


In [ ]:

# END!!!
